## Covid-19 Data Analysis

Dataset from - https://github.com/owid/covid-19-data/tree/master/public/data

1. Understanding Our Data
2. Covid 19 World Analysis - Most Recent Info
3. World Covid-19 Growth Over Time
4. Confirmed Cases in Each Country
5. Mapping Covid Around the World
6. Evolution of Confirmed Cases PM
7. Comparing Continents & Countries
8. Preparing Dataset for Flourish Bar Chart Race
9. Flourish - Making a Covid Bar Chart Race

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import seaborn as sns

## because we're pulling from the url, the data will always be up to date
url='https://covid.ourworldindata.org/data/owid-covid-data.csv'
df = pd.read_csv(url)
df.head()

iso_code continent  ... human_development_index excess_mortality
0      AFG      Asia  ...                   0.511              NaN
1      AFG      Asia  ...                   0.511              NaN
2      AFG      Asia  ...                   0.511              NaN
3      AFG      Asia  ...                   0.511              NaN
4      AFG      Asia  ...                   0.511              NaN

[5 rows x 62 columns]

In [2]:
df.info

<bound method DataFrame.info of        iso_code continent  ... human_development_index excess_mortality
0           AFG      Asia  ...                   0.511              NaN
1           AFG      Asia  ...                   0.511              NaN
2           AFG      Asia  ...                   0.511              NaN
3           AFG      Asia  ...                   0.511              NaN
4           AFG      Asia  ...                   0.511              NaN
...         ...       ...  ...                     ...              ...
109513      ZWE    Africa  ...                   0.571              NaN
109514      ZWE    Africa  ...                   0.571              NaN
109515      ZWE    Africa  ...                   0.571              NaN
109516      ZWE    Africa  ...                   0.571              NaN
109517      ZWE    Africa  ...                   0.571              NaN

[109518 rows x 62 columns]>

In [3]:
df[df['location'] == "Canada"]

iso_code      continent  ... human_development_index excess_mortality
17676      CAN  North America  ...                   0.929             4.03
17677      CAN  North America  ...                   0.929              NaN
17678      CAN  North America  ...                   0.929              NaN
17679      CAN  North America  ...                   0.929              NaN
17680      CAN  North America  ...                   0.929              NaN
...        ...            ...  ...                     ...              ...
18238      CAN  North America  ...                   0.929              NaN
18239      CAN  North America  ...                   0.929              NaN
18240      CAN  North America  ...                   0.929              NaN
18241      CAN  North America  ...                   0.929              NaN
18242      CAN  North America  ...                   0.929              NaN

[567 rows x 62 columns]

### Summary of the data:

In [4]:
## We'll use list comprehension to perform this 
## Since there we have quite a few null values, we'll use .isna() to find these values
## Then use the .mean function to get the average
## occurence and then multiply by 100 to convert to a percentage

NAN = [(c, df[c].isna().mean()*100) for c in df]

## Name the columns appropriately

NAN = pd.DataFrame(NAN, columns=["column_name", "percentage"])
NAN

column_name  percentage
0                     iso_code    0.000000
1                    continent    4.624811
2                     location    0.000000
3                         date    0.000000
4                  total_cases    4.285140
..                         ...         ...
57      handwashing_facilities   55.187275
58  hospital_beds_per_thousand   18.823390
59             life_expectancy    5.092314
60     human_development_index   10.692306
61            excess_mortality   96.462682

[62 rows x 2 columns]

In [5]:
# let's get an idea of how many countries we have in the dataset
print(df['location'].unique())
print(len(df['location'].unique()))

['Afghanistan' 'Africa' 'Albania' 'Algeria' 'Andorra' 'Angola' 'Anguilla'
 'Antigua and Barbuda' 'Argentina' 'Armenia' 'Aruba' 'Asia' 'Australia'
 'Austria' 'Azerbaijan' 'Bahamas' 'Bahrain' 'Bangladesh' 'Barbados'
 'Belarus' 'Belgium' 'Belize' 'Benin' 'Bermuda' 'Bhutan' 'Bolivia'
 'Bonaire Sint Eustatius and Saba' 'Bosnia and Herzegovina' 'Botswana'
 'Brazil' 'British Virgin Islands' 'Brunei' 'Bulgaria' 'Burkina Faso'
 'Burundi' 'Cambodia' 'Cameroon' 'Canada' 'Cape Verde' 'Cayman Islands'
 'Central African Republic' 'Chad' 'Chile' 'China' 'Colombia' 'Comoros'
 'Congo' 'Cook Islands' 'Costa Rica' "Cote d'Ivoire" 'Croatia' 'Cuba'
 'Curacao' 'Cyprus' 'Czechia' 'Democratic Republic of Congo' 'Denmark'
 'Djibouti' 'Dominica' 'Dominican Republic' 'Ecuador' 'Egypt'
 'El Salvador' 'Equatorial Guinea' 'Eritrea' 'Estonia' 'Eswatini'
 'Ethiopia' 'Europe' 'European Union' 'Faeroe Islands' 'Falkland Islands'
 'Fiji' 'Finland' 'France' 'French Polynesia' 'Gabon' 'Gambia' 'Georgia'
 'Germany' 'Ghana'

232 countries but we see that there is "World" and "International"

- let's delete world summary figures
- we should also delete the continents as well

In [6]:
df.drop(df[df.location == "Africa"].index, inplace=True)
df.drop(df[df.location == "Europe"].index, inplace=True)
df.drop(df[df.location == "North America"].index, inplace=True)
df.drop(df[df.location == "South America"].index, inplace=True)
df.drop(df[df.location == "European Union"].index, inplace=True)
df.drop(df[df.location == "World"].index, inplace=True)
df.drop(df[df.location == "Asia"].index, inplace=True)

In [7]:

# getting the most recent date (max gives you the latest date)
df_most_recent = df[df['date'] == max(df['date'])].reset_index()

df_most_recent.head()

index iso_code  ... human_development_index excess_mortality
0    537      AFG  ...                   0.511              NaN
1   1623      ALB  ...                   0.795              NaN
2   2160      DZA  ...                   0.748              NaN
3   2691      AND  ...                   0.868              NaN
4   3204      AGO  ...                   0.581              NaN

[5 rows x 63 columns]

### Create summary table

In [8]:
df_world = df_most_recent.groupby(["date"])[["total_cases","new_cases","new_deaths","total_deaths"]].sum().reset_index()

# Create Column headers/labels
labels = ["Last Update", "Total Confirmed","New Cases","New Deaths","Total Deaths"]

fig = go.Figure(data=[go.Table(header = dict(values=labels),
                 cells=dict(values=df_world.loc[0,["date","total_cases","new_cases","new_deaths","total_deaths"]]))
                     ])
fig.update_layout(title='Covid-19 World Summary: ',)
fig.show()

20,868 people died yesterday, August 12, 2021 from covid-19. 

In total 9.4 million people have died from covid.

## 3. World Covid-19 Growth Over Time

In [9]:
df_over_time = df.groupby(["date"])[["total_cases", "new_cases", "total_deaths", "new_deaths"]].sum().reset_index().sort_values("date", ascending=True).reset_index(drop=True)

In [10]:
df_over_time

date  total_cases  new_cases  total_deaths  new_deaths
0    2020-01-01          0.0        0.0           0.0         0.0
1    2020-01-02          0.0        0.0           0.0         0.0
2    2020-01-03          0.0        0.0           0.0         0.0
3    2020-01-04          0.0        0.0           0.0         0.0
4    2020-01-05          0.0        0.0           0.0         0.0
..          ...          ...        ...           ...         ...
587  2021-08-10  204117732.0   638009.0     4316018.0     11578.0
588  2021-08-11  204825644.0   707912.0     4325989.0      9971.0
589  2021-08-12  205511337.0   685693.0     4336284.0     10295.0
590  2021-08-13  206352879.0   841542.0     4347559.0     11275.0
591  2021-08-14  206852520.0   499641.0     4356150.0      8591.0

[592 rows x 5 columns]

## Confirmed Cases starting from day Zero (first covid case reported)

In [11]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_over_time.index, y=df_over_time['total_cases'],
                         mode='lines',
                         name="Confirmed cases"))

fig.update_layout(
    title="Evolution of Confirmed Covid-19 cases over time in the world",
    template="plotly_white",
    yaxis_title="Confirmed Cases",
    xaxis_title="Days",
)

fig.show()

Using Date axis instead of Days

In [12]:
fig = go.Figure(go.Bar(
    x=df_over_time['date'],
    y = df_over_time['total_cases'],
))

fig.update_layout(
    title="Confirmed Cases in Each Day",
    template='plotly_white',
    xaxis_title = "Confirmed Cases",
    yaxis_title="Days",
)

fig.show()

In [13]:
# let's see another layout with plotly just for fun.
# also need practice writing these plotly commands. repetition is key 

fig = go.Figure()

fig.add_trace(go.Scatter(x=df_over_time.index, y=df_over_time['total_deaths'],
                         mode='lines',marker_color='red',
                         name='Total Deaths',line=dict(dash='dot')))

fig.update_layout(
    title="Evolution of Covid-19 Deaths vs Confirmed Cases Over Time in the World",
    template="plotly_dark",
    yaxis_title="Number of Deaths",
    xaxis_title="Days",
)

fig.show()

Let's check ouf the new cases over time now

In [14]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_over_time.date, y=df_over_time['new_cases'],
                         mode='lines', marker_color='green',
                         name="New Covid Cases Daily", line=dict(dash="dot")))

fig.update_layout(
    title="Evolution of Covid-19 New Cases Over Time in the World",
    template="plotly_dark",
    yaxis_title="New Cases",
    xaxis_title="Days",
)

fig.show()

In [15]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_over_time.date, y=df_over_time['new_deaths'],
                    mode='lines',marker_color='red',
                    name='New Case Daily',line=dict( dash='dot')))

fig.update_layout(
    title='Evolution of Covid-19 New Deaths over time in the world',
        template='plotly_dark',
      yaxis_title="New Deaths",
    xaxis_title="Days",

)

fig.show()

## 4. Confirmed Cases in Each Country

In [16]:
df_per_country = df.groupby(['location'])['new_cases', 'new_deaths'].sum().reset_index().sort_values("new_cases", ascending=False).reset_index(drop=True)

df_per_country.head(10)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



location   new_cases  new_deaths
0   United States  36636852.0    621226.0
1           India  32192576.0    431225.0
2          Brazil  20350142.0    568788.0
3          France   6819929.0    112705.0
4          Russia   6490421.0    166795.0
5  United Kingdom   6270673.0    131210.0
6          Turkey   5236551.0     53005.0
7       Argentina   5080908.0    108936.0
8        Colombia   4864629.0    123356.0
9           Spain   4693540.0     82470.0

In [17]:
# Let's make column names better and get rid of decimal points

In [18]:
df_per_country.columns = ['Country', 'Total Cases', 'Total Deaths']
df_per_country = df_per_country.astype({"Country": str, "Total Cases": int, "Total Deaths": int})
df_per_country.head(5)

Country  Total Cases  Total Deaths
0  United States     36636852        621226
1          India     32192576        431225
2         Brazil     20350142        568788
3         France      6819929        112705
4         Russia      6490421        166795

### Let's display this as a barchart to see things in perspective

In [19]:
fig = go.Figure(go.Bar(
            x=df_per_country['Total Cases'],
            y=df_per_country['Country'],
            orientation='h'))
fig.update_layout(
    title='Confirmed Cases In Each Country',
    template='plotly_white',
     xaxis_title="Confirmed Cases",
    yaxis_title="Countries",
)
fig.show()

plotly cleans the graph nicely. Unfortuantely we can't specify which countries we want to see, but they selected the country names at random.

In [20]:
fig = go.Figure(go.Bar(
            x=df_per_country['Total Deaths'],
            y=df_per_country['Country'],
            orientation='h',
            marker_color='black'))
fig.update_layout(
    title='Deaths in Each Country',
    template='plotly_white',
     xaxis_title="Deaths",
    yaxis_title="Countries",
)
fig.show()

## 5. Mapping Covid-19 Across the World

Let's look at total case numbers on a world map

In [21]:
fig = px.choropleth(df_per_country, locations=df_per_country["Country"],
                    color=df_per_country['Total Cases'], locationmode='country names',
                    hover_name = df_per_country["Country"],
                    color_continuous_scale = px.colors.sequential.OrRd, template='plotly_dark',
                    ) 

fig.update_layout(
    title='Confirmed Cases in Each Country',
)
fig.show()

Let's adjust for population sizes as the above doesn't look very representative

In [22]:
df.head()

iso_code continent  ... human_development_index excess_mortality
0      AFG      Asia  ...                   0.511              NaN
1      AFG      Asia  ...                   0.511              NaN
2      AFG      Asia  ...                   0.511              NaN
3      AFG      Asia  ...                   0.511              NaN
4      AFG      Asia  ...                   0.511              NaN

[5 rows x 62 columns]

We have total casese pr million as a column. Let's use that

In [23]:
# group by country and get the total number of cases ad deaths per million

df_per_country_pm = df.groupby(['location'])['new_cases_per_million','new_deaths_per_million'].sum().reset_index().sort_values("new_cases_per_million", ascending=False).reset_index(drop=True)
df_per_country_pm.columns = ['Country', 'Total Cases PM', 'Total Deaths PM']
df_per_country_pm = df_per_country_pm.astype({"Country": str, "Total Cases PM": int, "Total Deaths PM": int})
df_per_country_pm.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



Country  Total Cases PM  Total Deaths PM
0     Andorra          193153             1669
1  Seychelles          192139              996
2  Montenegro          168375             2614
3     Bahrain          159155              813
4     Czechia          156511             2836

In [24]:
# let's use this df to do the same map as before
fig = px.choropleth(df_per_country_pm, locations=df_per_country_pm["Country"],
                    color=df_per_country_pm['Total Cases PM'], locationmode='country names',
                    hover_name = df_per_country_pm["Country"],
                    color_continuous_scale = px.colors.sequential.Viridis, template='plotly_dark',
                    ) 

fig.update_layout(
    title='Confirmed Cases Per Million in Each Country',
)
fig.show()

Let's look at the top 10 countries per million on a Scatter Plot

In [25]:
fig = go.Figure(data=[go.Scatter(
    x=df_per_country_pm['Country'][0:10],
    y=df_per_country_pm["Total Cases PM"][0:10],
    mode='markers',
    marker=dict(
        color=100+np.random.randn(1500),
        size=(df_per_country_pm['Total Cases PM'][0:10]/1500), # Change 1500 to larger as data evolves
        showscale=True
    )
)])

fig.update_layout(
    title="Most Infected Countries PM",
    xaxis_title="Countries",
    yaxis_title="Total Cases PM",
    template='plotly_white'
)

fig.show()

In [26]:
# Sort in descending order

df_per_country_pm = df_per_country_pm.sort_values(by="Total Deaths PM", ascending=False)

fig = go.Figure(data=[go.Scatter(
    x=df_per_country_pm['Country'][0:10],
    y=df_per_country_pm['Total Deaths PM'][0:10],
    mode='markers',
    marker=dict(
        color=df_per_country_pm['Total Cases PM'],
        size=(df_per_country_pm['Total Deaths PM'][0:10]/100), # change number to larger as data evolves
        showscale=True
    )
)])

fig.update_layout(
    title="Most Affected Countries by Deaths PM",
    xaxis_title="Countries",
    yaxis_title="Total Deaths PM",
    template='plotly_white',
)

fig.show()

## 6. Evolution of Confirmed Cases PM

In [27]:
df.tail()

iso_code continent  ... human_development_index excess_mortality
109513      ZWE    Africa  ...                   0.571              NaN
109514      ZWE    Africa  ...                   0.571              NaN
109515      ZWE    Africa  ...                   0.571              NaN
109516      ZWE    Africa  ...                   0.571              NaN
109517      ZWE    Africa  ...                   0.571              NaN

[5 rows x 62 columns]

In [28]:
fig = px.choropleth(df, locations = df['location'],
                    color = df['total_cases'], locationmode='country names',
                    hover_name = df['location'],
                    color_continuous_scale = px.colors.sequential.Inferno,
                    animation_frame = 'date')

fig.update_layout(
    title="Evolution of Confirmed Cases in each Country",
    template = "plotly_dark"
)

fig.show()

In [29]:
fig = px.choropleth(df, locations = df['location'],
                    color = df['total_cases_per_million'],locationmode='country names', 
                    hover_name = df['location'], 
                    color_continuous_scale = px.colors.sequential.GnBu,
                    animation_frame="date")
fig.update_layout(

    title='Evolution of total cases per million in each country',
    template='plotly_white'
)
fig.show()

## 7. Comparing Continents and Countries

In [30]:
df.head()

iso_code continent  ... human_development_index excess_mortality
0      AFG      Asia  ...                   0.511              NaN
1      AFG      Asia  ...                   0.511              NaN
2      AFG      Asia  ...                   0.511              NaN
3      AFG      Asia  ...                   0.511              NaN
4      AFG      Asia  ...                   0.511              NaN

[5 rows x 62 columns]

In [31]:
df_per_country_pm = df.groupby(['continent'])['new_cases_per_million', 'new_deaths_per_million'].sum().reset_index().sort_values('new_cases_per_million', ascending=False).reset_index(drop=True)
df_per_country_pm.columns = ['Country', 'Total Cases PM', 'Total Deaths PM']
df_per_country_pm = df_per_country_pm.astype({"Country": str, "Total Cases PM": int, "Total Deaths PM": int})
df_per_country_pm.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



Country  Total Cases PM  Total Deaths PM
0         Europe         3843924            68577
1           Asia         1703616            17455
2  South America          783455            24170
3  North America          744063            14052
4         Africa          702649            11371

First let's compare USA vs the Rest of the World

In [32]:
df_usa = df[df['location'] == "United States"]
df_usa.head()

iso_code      continent  ... human_development_index excess_mortality
103784      USA  North America  ...                   0.926              NaN
103785      USA  North America  ...                   0.926              NaN
103786      USA  North America  ...                   0.926              NaN
103787      USA  North America  ...                   0.926              NaN
103788      USA  North America  ...                   0.926             0.75

[5 rows x 62 columns]

In [33]:
url='https://covid.ourworldindata.org/data/owid-covid-data.csv'
df = pd.read_csv(url)

df_world = df[df['location'] == "World"]
df_world.head()

iso_code continent  ... human_development_index excess_mortality
107427  OWID_WRL       NaN  ...                   0.737              NaN
107428  OWID_WRL       NaN  ...                   0.737              NaN
107429  OWID_WRL       NaN  ...                   0.737              NaN
107430  OWID_WRL       NaN  ...                   0.737              NaN
107431  OWID_WRL       NaN  ...                   0.737              NaN

[5 rows x 62 columns]

In [34]:
df_india = df[df['location'] == "India"]
df_india.head()

iso_code continent  ... human_development_index excess_mortality
45250      IND      Asia  ...                   0.645              NaN
45251      IND      Asia  ...                   0.645              NaN
45252      IND      Asia  ...                   0.645              NaN
45253      IND      Asia  ...                   0.645              NaN
45254      IND      Asia  ...                   0.645              NaN

[5 rows x 62 columns]

In [35]:
fig = go.Figure()

fig.add_trace(go.Scatter(x = df_usa['date'], y= df_usa['total_cases'],
                         mode='lines',
                         name='Confirmed Cases in US'))

fig.add_trace(go.Scatter(x = df_india['date'], y= df_india['total_cases'],
                         mode='lines',
                         name='Confirmed Cases in India'))

fig.add_trace(go.Scatter(x = df_world['date'], y= df_world['total_cases'],
                         mode='lines',
                         name='Confirmed Cases in the rest of the World'))

fig.update_layout(
    title='Evolution of Confirmed cases over time in the US and the Rest of the World',
    template='plotly_white'
)

fig.show()

Let's compare deaths in the US vs the Rest of the World

In [36]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_usa['date'], y = df_usa['total_deaths'],
                         mode='lines',
                         name='Confirmed Deaths in the US'))

fig.add_trace(go.Scatter(x=df_world['date'], y = df_world['total_deaths'],
                         mode='lines',
                         name='Confirmed Deaths in the rest of the world'))

fig.update_layout(
    title='Evolution of Confirmed Deaths over time in US and The Rest Of The Word',
        template='plotly_white'

)

fig.show()


# Let's create a dataset we can import into Flourish

In [57]:
url='https://covid.ourworldindata.org/data/owid-covid-data.csv'
df = pd.read_csv(url)
df.head()

iso_code continent  ... human_development_index excess_mortality
0      AFG      Asia  ...                   0.511              NaN
1      AFG      Asia  ...                   0.511              NaN
2      AFG      Asia  ...                   0.511              NaN
3      AFG      Asia  ...                   0.511              NaN
4      AFG      Asia  ...                   0.511              NaN

[5 rows x 62 columns]

We'll have to wrangle the data bit to meet the flourish requirements

- country
- image URL (country)
- dates

In [58]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109518 entries, 0 to 109517
Data columns (total 62 columns):
 #   Column                                 Non-Null Count   Dtype  
---  ------                                 --------------   -----  
 0   iso_code                               109518 non-null  object 
 1   continent                              104453 non-null  object 
 2   location                               109518 non-null  object 
 3   date                                   109518 non-null  object 
 4   total_cases                            104825 non-null  float64
 5   new_cases                              104822 non-null  float64
 6   new_cases_smoothed                     103812 non-null  float64
 7   total_deaths                           94384 non-null   float64
 8   new_deaths                             94539 non-null   float64
 9   new_deaths_smoothed                    103812 non-null  float64
 10  total_cases_per_million                104270 non-null  

In [59]:
# let's start with changing the date format from object to datetime

df['date'] = pd.to_datetime(df.date)

# change format 
df['date'] = df['date'].dt.strftime('%y/%m/%d')
df.head()

iso_code continent  ... human_development_index excess_mortality
0      AFG      Asia  ...                   0.511              NaN
1      AFG      Asia  ...                   0.511              NaN
2      AFG      Asia  ...                   0.511              NaN
3      AFG      Asia  ...                   0.511              NaN
4      AFG      Asia  ...                   0.511              NaN

[5 rows x 62 columns]

In [60]:
# Let's set the date as the index
df = df.set_index('date')
df.head()

iso_code continent  ... human_development_index  excess_mortality
date                         ...                                          
20/02/24      AFG      Asia  ...                   0.511               NaN
20/02/25      AFG      Asia  ...                   0.511               NaN
20/02/26      AFG      Asia  ...                   0.511               NaN
20/02/27      AFG      Asia  ...                   0.511               NaN
20/02/28      AFG      Asia  ...                   0.511               NaN

[5 rows x 61 columns]

In [61]:
df_flourish = pd.pivot_table(df,values='total_cases',
                             index=['location'],
                             columns='date').reset_index()
df_flourish = df_flourish.fillna(0)
df_flourish.head()

date     location  20/01/22  20/01/23  ...   21/08/12   21/08/13   21/08/14
0     Afghanistan       0.0       0.0  ...   151563.0   151770.0   151770.0
1          Africa       0.0       0.0  ...  7164329.0  7204781.0  7238561.0
2         Albania       0.0       0.0  ...   134761.0   135140.0   135550.0
3         Algeria       0.0       0.0  ...   185042.0   185902.0   186655.0
4         Andorra       0.0       0.0  ...    14908.0    14924.0    14924.0

[5 rows x 572 columns]

Let's use the flags in our plot for countries

In [62]:
file_name = "https://raw.githubusercontent.com/rajeevratan84/covid/master/flags_world.csv"
flags = pd.read_csv(file_name)
flags

country                                          Image URL
0     Afghanistan  https://upload.wikimedia.org/wikipedia/commons...
1          Angola  https://cdn.countryflags.com/thumbs/angola/fla...
2         Albania  https://cdn.countryflags.com/thumbs/albania/fl...
3         Andorra  https://cdn.countryflags.com/thumbs/andorra/fl...
4       Argentina  https://cdn.countryflags.com/thumbs/argentina/...
..            ...                                                ...
203        Kosovo  https://cdn.countryflags.com/thumbs/kosovo/fla...
204   Yemen, Rep.       https://flagpedia.net/data/flags/w580/ye.png
205  South Africa  https://cdn.countryflags.com/thumbs/south-afri...
206        Zambia  https://cdn.countryflags.com/thumbs/zambia/fla...
207      Zimbabwe  https://cdn.countryflags.com/thumbs/zimbabwe/f...

[208 rows x 2 columns]

## Merging our data with the flag URL dataset

In [63]:
# merge flag onto flourish df
df_flourish = pd.merge(df_flourish, flags, left_on='location', right_on='country')

df_flourish.head()

location  ...                                          Image URL
0  Afghanistan  ...  https://upload.wikimedia.org/wikipedia/commons...
1      Albania  ...  https://cdn.countryflags.com/thumbs/albania/fl...
2      Algeria  ...  https://cdn.countryflags.com/thumbs/algeria/fl...
3      Andorra  ...  https://cdn.countryflags.com/thumbs/andorra/fl...
4       Angola  ...  https://cdn.countryflags.com/thumbs/angola/fla...

[5 rows x 574 columns]

In [44]:
# bring image url to second column between location and jan 1
# we have extra country column we don't need

Generating our final file for flourish

In [64]:
from datetime import datetime

# use current date for timestamped filename 
dateTimeObj = datetime.now()
timestampStr = dateTimeObj.strftime('%d_%b_%Y')

# delete unnecessary columns
# del df_flourish['country']

# Create a series to hold the image urls
mid = df_flourish['Image URL']

# delete the existing image urls
df_flourish.drop(labels=['Image URL'], axis=1, inplace=True)

# Insert Mid into the second position in the dataframe 
df_flourish.insert(1, 'Image URL', mid)

# Give the CSV a name with the current timestamp
csv_name = 'world_covid_cases_' +timestampStr + '.csv'
df_flourish.to_csv(csv_name)
from google.colab import files
files.download(csv_name)
df_flourish.head()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

location  ...      country
0  Afghanistan  ...  Afghanistan
1      Albania  ...      Albania
2      Algeria  ...      Algeria
3      Andorra  ...      Andorra
4       Angola  ...       Angola

[5 rows x 574 columns]

Index(['07/12/21', '07/13/20', '07/13/21', '07/14/20', '07/14/21', '07/15/20',
       '07/15/21', '07/16/20', '07/16/21', '07/17/20',
       ...
       '12/23/20', '12/24/20', '12/25/20', '12/26/20', '12/27/20', '12/28/20',
       '12/29/20', '12/30/20', '12/31/20', 'country'],
      dtype='object', length=207)

In [ ]:
# f.to_csv('sample.csv')
# from google.colab import files
# files.download("sample.csv")